# extern

In [1]:
import os
os.environ['PATH'] += ':/usr/local/cuda/bin' # 保证 nvcc 可以被找到
import tvm
from tvm import te
import numpy as np
import tvm.testing

验证 TVM 在不同目标设备上的向量化代码生成能力。测试分为 CPU 和 GPU 两个版本：CPU 版本使用循环展开策略处理向量化计算，GPU 版本通过线程块和线程索引实现并行。核心逻辑通过手动构建 TIR 中间表示，验证生成代码在 LLVM/OpenCL/CUDA 后端的正确性。测试使用 `te.extern` 创建外部计算节点，并检查输出结果是否符合预期。

CPU 版本：使用 SIMD 向量化策略（`float32x2`），每次迭代处理 2 个元素，实现 2 倍循环展开

In [2]:
def extern_generator(ins, outs):
    """Manually write the IR for the extern function, add pipeline"""
    ib = tvm.tir.ir_builder.create()
    with ib.for_range(0, (n + 1) // 2) as i:
        ib.emit(
            outs[0].vstore(
                i * 2, ins[0].vload(i * 2, "float32x2") + tvm.tir.const(1, "float32x2")
            )
        )
    return ib.get()

GPU 版本：通过 `blockIdx.x` 和 `threadIdx.x` 实现两级并行，适配 GPU 的 SIMT 架构

In [3]:
def extern_generator_gpu(ins, outs):
    """Manually write the IR for the extern function, add pipeline"""
    ib = tvm.tir.ir_builder.create()
    bx = te.thread_axis("blockIdx.x")
    tx = te.thread_axis("threadIdx.x")
    ib.scope_attr(bx, "thread_extent", (nn + max_threads - 1) // max_threads)
    ib.scope_attr(tx, "thread_extent", max_threads)
    idx = bx.var * max_threads + tx.var
    with ib.if_scope(ib.likely(idx < n)):
        ib.emit(
            outs[0].vstore(
                idx * 2, ins[0].vload(idx * 2, "float32x2") + tvm.tir.const(1, "float32x2")
            )
        )
    return ib.get()

- `te.extern` 创建外部计算节点，分离计算定义与实现
- `vload/vstore` 实现显式向量化内存访问
- 内存对齐：向量化访问要求 64 位对齐（`float32x2`对应 `2*4B=8B`）

In [4]:
nn = 64
max_threads = 4
n = tvm.runtime.convert(nn)
A = te.placeholder((n,), name="A")

C_cpu = te.extern(A.shape, [A], extern_generator, name="C")
C_gpu = te.extern(A.shape, [A], extern_generator_gpu, name="C")

# Create IRModules directly
mod_cpu = tvm.IRModule.from_expr(te.create_prim_func([A, C_cpu]))
mod_gpu = tvm.IRModule.from_expr(te.create_prim_func([A, C_gpu]))

In [5]:
mod_cpu.show()

In [6]:
mod_gpu.show()

跨设备统一验证：

In [7]:
def check_target(target):
    if not tvm.testing.device_enabled(target):
        return
    mod = mod_gpu if target in ["opencl", "cuda"] else mod_cpu
    C = C_gpu if target in ["opencl", "cuda"] else C_cpu
    # build and invoke the kernel.
    f = tvm.compile(mod, target=target)
    dev = tvm.device(target, 0)
    # launch the kernel.
    n = nn
    a = tvm.nd.array(np.random.uniform(size=n).astype(A.dtype), dev)
    c = tvm.nd.array(np.zeros(n, dtype=C.dtype), dev)
    f(a, c)
    tvm.testing.assert_allclose(c.numpy(), a.numpy() + 1)

In [8]:
check_target("llvm")
check_target("opencl")
check_target("cuda")

## 打包 buffer 

In [9]:
def extern_generator(ins, outs):
    """Manually write the IR for the extern function, add pipeline."""
    return tvm.tir.call_packed("my_extern_array_func1", ins[0], outs[0])

In [10]:
nn = 1024
n = tvm.runtime.convert(nn)
A = te.placeholder((n,), name="A")
C = te.extern(A.shape, [A], extern_generator, name="C")

# Create IRModule directly
mod = tvm.IRModule.from_expr(te.create_prim_func([A, C]))
mod.show()

In [11]:
@tvm.register_func
def my_extern_array_func1(aa, bb):
    aa.copyto(bb)

In [12]:
def check_target(target):
    if not tvm.testing.device_enabled(target):
        return
    # build and invoke the kernel.
    f = tvm.compile(mod, target=target)
    dev = tvm.cpu(0)
    # launch the kernel.
    n = nn
    a = tvm.nd.array(np.random.uniform(size=n).astype(A.dtype), dev)
    c = tvm.nd.array(np.zeros(n, dtype=C.dtype), dev)

    f(a, c)
    tvm.testing.assert_allclose(c.numpy(), a.numpy())

check_target("llvm")

## 打包缓冲区中间表示

In [13]:
def extern_generator(ins, outs):
    """Manually write the IR for the extern function, add pipeline."""
    return tvm.tir.call_packed("my_extern_array_func2", *ins, outs[0])

In [15]:
nn = 1024
n = tvm.runtime.convert(nn)
A = te.placeholder((n,), name="A")
B = te.compute((n,), lambda i: A[i] + 1, name="B")
C = te.extern(B.shape, [B], extern_generator, name="C")
# D = te.compute((n,), lambda i: C[i] + 1, name="D")
mod = tvm.IRModule.from_expr(te.create_prim_func([A, C]))
mod.show()

In [16]:
def check_target(target):
    if not tvm.testing.device_enabled(target):
        return
    # build and invoke the kernel.
    f = tvm.compile(mod, target=target)
    dev = tvm.cpu(0)
    # launch the kernel.
    n = nn
    a = tvm.nd.array(np.random.uniform(size=n).astype(A.dtype), dev)
    b = tvm.nd.array(np.zeros(n, dtype=B.dtype), dev)
    c = tvm.nd.array(np.zeros(n, dtype=C.dtype), dev)

    @tvm.register_func
    def my_extern_array_func2(aa, cc):
        assert aa.shape == a.shape
        tvm.testing.assert_allclose(aa.numpy(), a.numpy()+1)
        aa.copyto(cc)

    f(a, c)
    tvm.testing.assert_allclose(c.numpy(), a.numpy() + 1)

In [17]:
check_target("llvm")

InternalError: Check failed: undefined.size() == 0 (1 vs. 0) : In PrimFunc main variables [elem_offset] are used, but are not passed in as API arguments